In [1]:
import torch
import torch.nn as nn
import pandas as pd
import numpy as np



In [2]:
df = pd.read_csv("./combined_tweets_2020_labeled.csv", index_col = 0)


In [63]:
df.head()

date                                         text_split  label_up5  \
0  2020-01-01  is the year of bitcoin bitcoin is up in decade...      False   
1  2020-01-01  activity and bases when can print they need go...      False   
2  2020-01-01  address related to his announcement why they b...      False   
3  2020-01-01  xrp btc btc price action is similar to bitcoin...      False   
4  2020-01-01  about cryptocurrency and will be the beginning...      False   

   label_up2  label_down5  label_down2  
0      False        False        False  
1      False        False        False  
2      False        False        False  
3      False        False        False  
4      False        False        False

In [64]:
from transformers import pipeline
pipeline = pipeline('feature-extraction', model='yiyanghkust/finbert-pretrain')
data = pipeline("this is a test")
print(data)

[[[-0.811686098575592, 0.2049413025379181, -0.8654860854148865, 0.18978895246982574, 0.32066819071769714, -0.36538541316986084, -0.39698565006256104, 1.2678611278533936, -0.13200154900550842, -0.43081068992614746, 0.1527545303106308, 0.7017031311988831, 0.3456867039203644, -0.6038628220558167, -0.025148361921310425, -1.5150455236434937, 0.7829488515853882, -0.11538706719875336, 0.5935987234115601, 0.34115320444107056, -0.24202169477939606, 1.0729786157608032, 0.42335063219070435, 1.677152395248413, 0.1811797320842743, -0.12520819902420044, -0.8086816668510437, 0.4794812798500061, -1.2718595266342163, -0.5580711364746094, -0.21857097744941711, -0.7462496161460876, 0.2855101227760315, -0.148176372051239, -1.1218559741973877, -0.4778083562850952, 0.3890625536441803, 0.06391781568527222, 0.6200288534164429, -0.423489511013031, 0.7995272874832153, 0.9490830302238464, 0.018031811341643333, -0.26928234100341797, -1.3739815950393677, 0.7737358212471008, 0.23642289638519287, 0.08937901258468628

In [85]:
df["embeddings"] =0
df["torch_tensor"]=0

In [86]:
for i in range(0,111):
    # print(i)
    s = df.at[i,"text_split"]
    df.at[i,"embeddings"] =  pipeline(s)


In [87]:
zeros = [0 for i in range(768)]

In [88]:
#padding all input seqs to 362 by 0's
for i in range(1,111):
  diffn = 362 - len(df["embeddings"][i][0])
  for j in range(diffn):
    df["embeddings"][i][0].append(zeros)

In [89]:
df["final_label_2"]=0
df["final_label_5"]=0

In [90]:
type(df.iloc[0]["label_up2"])

numpy.bool_

In [91]:
for i in range(1,111):
  if((df.iloc[i]["label_up2"]==True) or (df.iloc[i]["label_down2"]==True)): 
    df.at[i,"final_label_2"]=1
  if((df.iloc[i]["label_up5"]==True) or (df.iloc[i]["label_down5"]==True)): 
    df.at[i,"final_label_5"]=1
  

In [92]:
trainData_2 = df[1:100][["embeddings","final_label_2"]]
testData_2=df[101:111][["embeddings","final_label_2"]]
trainData_5 = df[1:100][["embeddings","final_label_5"]]
testData_5=df[101:111][["embeddings","final_label_5"]]

In [96]:
# trainData_2.reset_index(inplace=True)
# trainData_5.reset_index(inplace=True)
# testData_2.reset_index(inplace=True)
# testData_5.reset_index(inplace=True)
testData_2.head()

embeddings  final_label_2
101  [[[-0.2342233657836914, -0.18213340640068054, ...              0
102  [[[-0.34318751096725464, -0.016853531822562218...              0
103  [[[-0.4612177908420563, -0.16559255123138428, ...              0
104  [[[-0.27222639322280884, 0.3325844407081604, -...              0
105  [[[-0.1867963820695877, 0.21999740600585938, -...              0

In [94]:
import csv

In [78]:
trainData_2.drop(columns=["level_0","index"])
trainData_5.drop(columns=["level_0","index"])
testData_2.drop(columns=["level_0","index"])
testData_5.drop(columns=["level_0","index"])

embeddings  final_label_5
0  [[[-0.2342233657836914, -0.18213340640068054, ...              0
1  [[[-0.34318751096725464, -0.016853531822562218...              0
2  [[[-0.4612177908420563, -0.16559255123138428, ...              0
3  [[[-0.27222639322280884, 0.3325844407081604, -...              0
4  [[[-0.1867963820695877, 0.21999740600585938, -...              0
5  [[[-0.32459506392478943, 0.24001923203468323, ...              0
6  [[[-0.5066268444061279, 0.21190214157104492, -...              0
7  [[[-0.4591989815235138, -0.08014729619026184, ...              0
8  [[[-0.43837106227874756, 0.0595862939953804, -...              0
9  [[[-0.312589168548584, -0.2782647907733917, -1...              0

In [95]:
trainData_2.to_pickle('trainData_2.pkl')
testData_2.to_pickle('testData_2.pkl')

trainData_5.to_pickle('trainData_5.pkl')

testData_5.to_pickle('testData_5.pkl')


In [36]:
type(testData_2["embeddings"][0][0][0][0])

float

In [23]:
trainData_5["final_label_5"].value_counts()

0    99
Name: final_label_5, dtype: int64

In [24]:
df["label_down2"].value_counts()

False    39076
True     25234
Name: label_down2, dtype: int64

In [39]:
trainData_2.head()

embeddings  final_label_2
1  [[[-0.5096779465675354, 0.01137804239988327, -...              0
2  [[[-0.05925348401069641, -0.010846097022294998...              0
3  [[[-0.43134886026382446, 0.038226477801799774,...              0
4  [[[-0.42397764325141907, 0.2199113667011261, -...              0
5  [[[-0.32623717188835144, 0.28235089778900146, ...              0

In [26]:
trainData_2.columns

Index(['embeddings', 'final_label_2'], dtype='object')

In [37]:
trainData = pd.read_csv('trainData_2.csv', index_col=0)


In [38]:
trainData.columns

Index(['final_label_2'], dtype='object')

In [42]:
trainData_5.head()

embeddings  final_label_5
1  [[[-0.5096779465675354, 0.01137804239988327, -...              0
2  [[[-0.05925348401069641, -0.010846097022294998...              0
3  [[[-0.43134886026382446, 0.038226477801799774,...              0
4  [[[-0.42397764325141907, 0.2199113667011261, -...              0
5  [[[-0.32623717188835144, 0.28235089778900146, ...              0

In [48]:
type(trainData_5.iloc[0]["embeddings"][0][0][0])

float

In [55]:
type(np.array(trainData_5["embeddings"][0][0][0][0]))

numpy.ndarray

In [43]:

# Assuming 'df' is your DataFrame and 'array_column' is the column containing NumPy arrays
testData_2['embeddings'] = testData_2['embeddings'].apply(lambda x: np.array2string(x, separator=','))



AttributeError: 'list' object has no attribute 'size'

In [44]:
testData_2.to_pickle('testData_2.pkl')


In [3]:
df2 = pd.read_pickle('testData_2.pkl')

# Convert the string representation back to NumPy arrays
df2.head()


embeddings  final_label_2
101  [[[-0.2342233657836914, -0.18213340640068054, ...              0
102  [[[-0.34318751096725464, -0.016853531822562218...              0
103  [[[-0.4612177908420563, -0.16559255123138428, ...              0
104  [[[-0.27222639322280884, 0.3325844407081604, -...              0
105  [[[-0.1867963820695877, 0.21999740600585938, -...              0

In [8]:
len(df2["embeddings"][101][0][0])

768

In [12]:
dtypes = {"embeddings":float,"final_label_2":float}

In [41]:
df = pd.read_csv("trainData_2.csv",index_col=0)

In [30]:
df.columns

Index(['embeddings', 'final_label_2'], dtype='object')

In [42]:
type(df["embeddings"][1][0][0])

str

In [8]:
len(df["embeddings"][0])

KeyError: 0

In [47]:
df2.head()

index                                         embeddings  final_label_2
0    101  [[[-0.2342233657836914, -0.18213340640068054, ...              0
1    102  [[[-0.34318751096725464, -0.016853531822562218...              0
2    103  [[[-0.4612177908420563, -0.16559255123138428, ...              0
3    104  [[[-0.27222639322280884, 0.3325844407081604, -...              0
4    105  [[[-0.1867963820695877, 0.21999740600585938, -...              0

In [50]:
df2 = df2.iloc[:,1:]

In [59]:
testData = pd.read_pickle('testData_2.pkl')


In [60]:
testData.head()

index                                         embeddings  final_label_2
0    101  [[[-0.2342233657836914, -0.18213340640068054, ...              0
1    102  [[[-0.34318751096725464, -0.016853531822562218...              0
2    103  [[[-0.4612177908420563, -0.16559255123138428, ...              0
3    104  [[[-0.27222639322280884, 0.3325844407081604, -...              0
4    105  [[[-0.1867963820695877, 0.21999740600585938, -...              0

In [57]:
testData.drop(columns={"index"},inplace= True)

In [55]:
testData["embeddings"][0]

[[[-0.2342233657836914,
   -0.18213340640068054,
   -0.5072378516197205,
   0.8489389419555664,
   1.57365083694458,
   -0.5821934938430786,
   -0.10513083636760712,
   0.7407779097557068,
   0.04486847296357155,
   0.0710441842675209,
   -0.15732182562351227,
   0.08077177405357361,
   0.7142284512519836,
   -0.08636346459388733,
   -0.3504146933555603,
   -0.0620296448469162,
   0.24521170556545258,
   -0.3627396523952484,
   -0.14080333709716797,
   -1.0229220390319824,
   -0.4430646002292633,
   0.2896009087562561,
   -0.7372846603393555,
   0.7651053071022034,
   0.1650768518447876,
   0.7476019859313965,
   -0.16586358845233917,
   0.5698671936988831,
   -0.17368535697460175,
   -1.2906765937805176,
   0.3363310694694519,
   -0.10000108927488327,
   0.21537339687347412,
   0.4655129015445709,
   0.19369666278362274,
   -0.2152584195137024,
   -0.4417930841445923,
   -1.0195398330688477,
   -0.4117564260959625,
   -0.5059357285499573,
   -0.273925244808197,
   0.529833197593689,
 

In [58]:
testData.head()

embeddings  final_label_2
0  [[[-0.2342233657836914, -0.18213340640068054, ...              0
1  [[[-0.34318751096725464, -0.016853531822562218...              0
2  [[[-0.4612177908420563, -0.16559255123138428, ...              0
3  [[[-0.27222639322280884, 0.3325844407081604, -...              0
4  [[[-0.1867963820695877, 0.21999740600585938, -...              0